# Build *Bacillus subtilis*

We will build an ME model from the NC_000913.2 Genbank file, the iJO1366
M model, and the complex reconstruction from iJL1678-ME

In [1]:
from __future__ import print_function, division, absolute_import

# python imports
import re
from os.path import join
from collections import defaultdict
import pickle

# third party imports
import pandas
import cobra

# COBRAme
import cobrame
from cobrame.util import building, mu, me_model_interface
from cobrame.io.json import save_json_me_model, save_reduced_json_me_model

# ECOLIme
import ecolime
from ecolime import (transcription, translation, flat_files, generics, formulas, compartments)
ecolime.__file__

/home/jt/Downloads/cobrapy-0.5.11/cobra/io/__init__.py:12: UserWarning: cobra.io.sbml requires libsbml
  warn("cobra.io.sbml requires libsbml")


'/home/jt/UCSD/bacillusme-master/ecolime/__init__.py'

## Part 1: Create minimum solveable ME-model
This will include the bare minimum representations of 
- Transcription Reactions
- Translation Reactions
- Complex Formation Reactions
- Metabolic Reactions

that still produce a working ME-model

### 1) Create Model Object and populate its global info
This includes important parameters that are used to calculate coupling 
constraints as well as organism-specific information such as peptide 
processing types

In [2]:
# Define Models
ijo_directory = join(flat_files.ecoli_files_dir, 'iYO844.json')
ijo = cobra.io.load_json_model(ijo_directory)
me = cobrame.MEModel('iYO844-ME')

# ME-models require special OptLang interface if cobrapy version >= 0.6.0
# If cannot import SymbolicParameter, assume using cobrapy
# versions <= 0.5.11
try:
    from optlang.interface import SymbolicParameter
except:
    pass
else:
    me.solver = me_model_interface

# "Translational capacity" of organism
me.global_info['kt'] = 4.5  # (in h-1)scott 2010, RNA-to-protein curve fit
me.global_info['r0'] = 0.087  # scott 2010, RNA-to-protein curve fit
me.global_info['k_deg'] = 1.0/5. * 60.0  # 1/5 1/min 60 min/h # h-1

# Molecular mass of RNA component of ribosome
me.global_info['m_rr'] = 1453. # in kDa

# Average molecular mass of an amino acid
me.global_info['m_aa'] = 109. / 1000.  # in kDa

# Proportion of RNA that is rRNA
me.global_info['f_rRNA'] = .86
me.global_info['m_nt'] = 324. / 1000.  # in kDa
me.global_info['f_mRNA'] = .02

# tRNA associated global information
me.global_info['m_tRNA'] = 25000. / 1000.  # in kDA
me.global_info['f_tRNA'] = .12

# Folding Properties
me.global_info['temperature'] = 37
me.global_info['propensity_scaling'] = .45

# DNA Replication Parameters
me.global_info['GC_fraction'] = 0.507896997096

# Define the types of biomass that will be synthesized in the model
me.add_biomass_constraints_to_model(["protein_biomass", "mRNA_biomass", "tRNA_biomass", "rRNA_biomass",
                                     "ncRNA_biomass", "DNA_biomass", "lipid_biomass", "constituent_biomass",
                                     "prosthetic_group_biomass", "peptidoglycan_biomass"])

# Define ME-model compartments
me.compartments = {"p": "Periplasm", "e": "Extra-organism", "c": "Cytosol", 
                   "im": 'Inner Membrane', 'om': "Outer Membrane", "mc": "ME-model Constraint",
                   "m": "Membrane"}

### 2) Load metabolites and build Metabolic reactions
The below reads in:
- Required 
 * **reaction_matrix.txt** (reaction matrix w/ reactions unlumped, metabolites renamed etc.)
 * **metabolites.txt** (metabolite properties)
 * **reactions.txt** (info on reversiblity, whether enzyme catalyzed etc.)
 * **m_to_me_mets.csv** (mapping of enzymes/complexes used in M-model to their ME-model compatible ID)
 * **protein_complexes.txt** (protein subunit stoichiometry of all complexes, used to identify metabolites as such)
 
It creates a new e coli M-model from this info then incorporates it into the ME-model using *add_m_model_content*. metabolites are added directly reactions are added as StoichiometricData

Metabolite types have different properties in an ME-model so enzyme complexes need added to the model as Complexes not Metabolites. Components in the E. coli M-model that are actually Complexes are compiled in *complex_list*

In [3]:
# m_model = flat_files.get_m_model()
m_model = flat_files.process_m_model(ijo, 'metabolites.txt',
                                     'm_to_me_mets.csv', 'reactions.txt',
                                     'reaction_matrix.txt',
                                     'protein_complexes.txt',
                                     defer_to_rxn_matrix=set())
m_model.reactions.EX_glc__D_e.id = 'EX_glc__D_e'
m_model.repair()
# some of the "metabolites" in iJO1366 "M" model are actually complexes. We pass those in
# so they get created as complexes, not metabolites.
complexes = flat_files.get_complex_subunit_stoichiometry(
    'protein_complexes.txt').keys()
complex_set = set(
    [i.id for i in m_model.metabolites if i.id.split('_mod_')[0] in complexes])
building.add_m_model_content(me, m_model, complex_metabolite_ids=complex_set)

/home/jt/UCSD/bacillusme-master/ecolime/corrections.py:34 UserWarning: Creating new metabolite (4fe4s_c)
/home/jt/UCSD/bacillusme-master/ecolime/corrections.py:34 UserWarning: Creating new metabolite (2fe2s_c)
/home/jt/UCSD/bacillusme-master/ecolime/corrections.py:34 UserWarning: Creating new metabolite (LI_c)
/home/jt/UCSD/bacillusme-master/ecolime/corrections.py:34 UserWarning: Creating new metabolite (3a1hac1p_c)


In [4]:
# This adds exchange reactions for metabolites not contained in iJO1366
# Some of these cannot be produced by the model so they are added here
exchange_list = [
    'LI_c',
    'pqq_e',
    'cs_e',
    'tl_c',
    'RNase_m5','RNase_m16','RNase_m23'] # RNAses are gaps in model

for met_id in exchange_list:
    r = cobrame.MEReaction("EX_" + met_id)
    me.add_reaction(r)
    r.reaction = met_id + " <=> "

unknown metabolite 'pqq_e' created
unknown metabolite 'cs_e' created
unknown metabolite 'tl_c' created
unknown metabolite 'RNase_m5' created
unknown metabolite 'RNase_m16' created
unknown metabolite 'RNase_m23' created


In [5]:
last = 1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

1
protein_biomass_to_biomass
protein_biomass --> biomass
2
mRNA_biomass_to_biomass
mRNA_biomass --> biomass
3
tRNA_biomass_to_biomass
tRNA_biomass --> biomass
4
rRNA_biomass_to_biomass
rRNA_biomass --> biomass
5
ncRNA_biomass_to_biomass
ncRNA_biomass --> biomass
6
DNA_biomass_to_biomass
DNA_biomass --> biomass
7
lipid_biomass_to_biomass
lipid_biomass --> biomass
8
constituent_biomass_to_biomass
constituent_biomass --> biomass
9
prosthetic_group_biomass_to_biomass
prosthetic_group_biomass --> biomass
10
peptidoglycan_biomass_to_biomass
peptidoglycan_biomass --> biomass
11
EX_2ddglcn_e
2ddglcn_e --> 
12
EX_2hxmp_e
2hxmp_e --> 
13
EX_2pg_e
2pg_e --> 
14
EX_2pglyc_e
2pglyc_e --> 
15
EX_3amba_e
3amba_e --> 
16
EX_3amp_e
3amp_e --> 
17
EX_3cmp_e
3cmp_e --> 
18
EX_3gmp_e
3gmp_e --> 
19
EX_3pg_e
3pg_e --> 
20
EX_3ump_e
3ump_e --> 
21
EX_4abut_e
4abut_e --> 
22
EX_5mtr_e
5mtr_e --> 
23
EX_6pgc_e
6pgc_e --> 
24
EX_Larab_e
Larab_e --> 
25
EX_Lcyst_e
Lcyst_e --> 
26
EX_abt__L_e
abt__L_e --> 
27
EX

### 3) Add Transcription and Translation 
The below reads in:
- Required
 * **NC_000913.2.gb** (Genbank sequence annotation)
 * **ecolime/translation.py** (codon to tRNA mapping)
- Optional
 * **TUs_from_ecocyc.txt** (TU definitions, start/stop positions, etc.)
 * **ecolime/translation.py** (dictionary of gene to frameshift mutation)
 
To construct the bare minimimum components of a transcription and translation reactions. For example, transcription reactions at this point include nucleotides and the synthesized RNAs.

In [6]:
from Bio import SeqIO
from cobrame.util import dogma

gb_filename = join(flat_files.ecoli_files_dir,'NC_000964.gb')     
gb_file = SeqIO.read(gb_filename, 'gb')
full_seq = str(gb_file.seq)

element_types={'CDS', 'rRNA','tRNA', 'ncRNA'}

frameshift_string={}
for feature in gb_file.features:
    if feature.type not in element_types or 'pseudo' in feature.qualifiers:
        continue
    bnum = feature.qualifiers["locus_tag"][0]
    seq = ''
    for location in feature.location.parts:
        left_pos = int(location.start)
        right_pos = int(location.end)
        strand = '+' if location.strand == 1 else '-'
        seq = dogma.extract_sequence(full_seq, left_pos, right_pos, strand) + seq 

In [7]:
gb_filename = join(flat_files.ecoli_files_dir,'NC_000964.gb')                                                                                    
tu_df = flat_files.get_tu_dataframe('TUs_from_bsubcyc.txt')

building.build_reactions_from_genbank(me, gb_filename, tu_df, verbose=False,
                                      frameshift_dict=translation.frameshift_dict,
                                      trna_to_codon=translation.trna_to_codon)



/home/jt/UCSD/cobrame-master/cobrame/core/reaction.py:852 UserWarning: RNA Polymerase () not found
/home/jt/UCSD/cobrame-master/cobrame/core/reaction.py:1093 UserWarning: ribosome not found
/home/jt/UCSD/cobrame-master/cobrame/core/reaction.py:1136 UserWarning: RNA_degradosome not found


In [8]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

247
transcription_TU8J2_1112_from_RpoD_mono
478 atp_c + 332 ctp_c + 328 gtp_c + 412 utp_c --> RNA_BSU_03540 + RNA_BSU_03550 + 479.80870261700005 mRNA_biomass + 1550 ppi_c
248
transcription_TU8J2_1243_from_RpoD_mono
186 atp_c + 122 ctp_c + 111 gtp_c + 154 utp_c --> RNA_BSU_23050 + 183.35422381299998 mRNA_biomass + 573 ppi_c
249
transcription_TU8J2_798_from_RpoD_mono
204 atp_c + 162 ctp_c + 116 gtp_c + 269 utp_c --> RNA_BSU_17900 + RNA_BSU_17910 + 211.50199622600002 mRNA_biomass + 751 ppi_c
250
transcription_TU8J2_569_from_RpoD_mono
812 atp_c + 820 ctp_c + 641 gtp_c + 963 utp_c --> RNA_BSU_29170 + RNA_BSU_29180 + RNA_BSU_29190 + 987.8044632220001 mRNA_biomass + 3236 ppi_c
251
transcription_TU8J2_1472_from_RpoD_mono
61 atp_c + 66 ctp_c + 47 gtp_c + 75 utp_c --> RNA_BSU_23040 + 79.159648349 mRNA_biomass + 249 ppi_c
252
transcription_TU8J2_1348_from_RpoD_mono
97 atp_c + 104 ctp_c + 106 gtp_c + 113 utp_c --> RNA_BSU_06540 + 134.43701480000001 mRNA_biomass + 420 ppi_c
253
transcription_TU8J2_

714 atp_c + 529 ctp_c + 473 gtp_c + 743 utp_c --> RNA_BSU_19750 + RNA_BSU_19760 + RNA_BSU_19770 + 755.6363203269999 mRNA_biomass + 2459 ppi_c
811
transcription_TU8J2_1078_from_RpoD_mono
911 atp_c + 933 ctp_c + 760 gtp_c + 1060 utp_c --> RNA_BSU_04450 + RNA_BSU_04460 + RNA_BSU_04470 + 1133.342473995 mRNA_biomass + 3664 ppi_c
812
transcription_TU8J2_302_from_RpoD_mono
143 atp_c + 231 ctp_c + 172 gtp_c + 232 utp_c --> RNA_BSU_38610 + RNA_BSU_38620 + 238.42807396999999 mRNA_biomass + 778 ppi_c
813
transcription_TU8J2_311_from_RpoD_mono
220 atp_c + 195 ctp_c + 164 gtp_c + 282 utp_c --> RNA_BSU_38430 + 274.020300881 mRNA_biomass + 861 ppi_c
814
transcription_TU8J2_1312_from_RpoD_mono
1147 atp_c + 1196 ctp_c + 1051 gtp_c + 1293 utp_c --> RNA_BSU_31540 + RNA_BSU_31550 + RNA_BSU_31560 + RNA_BSU_31570 + 1475.1340323800002 mRNA_biomass + 4687 ppi_c
815
transcription_TU8J2_533_from_RpoD_mono
464 atp_c + 352 ctp_c + 343 gtp_c + 380 utp_c --> RNA_BSU_30070 + 493.372646139 mRNA_biomass + 1539 ppi_c
8

1028 atp_c + 1539 ctp_c + 1139 gtp_c + 246 h2o_c + 1295 utp_c --> RNA_BSU_rRNA_1 + RNA_BSU_rRNA_2 + RNA_BSU_rRNA_3 + RNA_BSU_tRNA_5 + RNA_BSU_tRNA_6 + 90 amp_c + 39 cmp_c + 38 gmp_c + 246 h_c + 5001 ppi_c + 1465.0412734020001 rRNA_biomass + 49.101943713 tRNA_biomass + 79 ump_c
1311
transcription_TU8J2_459_from_RpoD_mono
523 atp_c + 471 ctp_c + 399 gtp_c + 637 utp_c --> RNA_BSU_33010 + RNA_BSU_33020 + 647.8763145739999 mRNA_biomass + 2030 ppi_c
1312
transcription_TU8J2_560_from_RpoD_mono
111 atp_c + 135 ctp_c + 108 gtp_c + 159 utp_c --> RNA_BSU_29460 + 163.186824753 mRNA_biomass + 513 ppi_c
1313
transcription_TU8J2_57_from_RpoD_mono
1334 atp_c + 1166 ctp_c + 1092 gtp_c + 1384 utp_c --> RNA_BSU_38500 + RNA_BSU_38510 + RNA_BSU_38520 + RNA_BSU_38530 + RNA_BSU_38540 + 1558.521395335 mRNA_biomass + 4976 ppi_c
1314
transcription_TU8J2_669_from_RpoD_mono
1162 atp_c + 958 ctp_c + 761 gtp_c + 1310 utp_c --> RNA_BSU_24660 + RNA_BSU_24670 + RNA_BSU_24680 + RNA_BSU_24690 + RNA_BSU_24700 + RNA_BSU_2

transcription_TU8J2_1054_from_RpoD_mono
538 atp_c + 576 ctp_c + 583 gtp_c + 793 utp_c --> RNA_BSU_06140 + 794.43177307 mRNA_biomass + 2490 ppi_c
1811
transcription_TU8J2_1404_from_RpoD_mono
352 atp_c + 212 ctp_c + 212 gtp_c + 247 utp_c --> RNA_BSU_13520 + 328.354326243 mRNA_biomass + 1023 ppi_c
1812
transcription_TU8J2_738_from_RpoD_mono
58 atp_c + 54 ctp_c + 48 gtp_c + 98 utp_c --> RNA_BSU_22020 + 81.88780753799999 mRNA_biomass + 258 ppi_c
1813
transcription_TU8J2_51_from_RpoD_mono
615 atp_c + 625 ctp_c + 467 gtp_c + 748 utp_c --> RNA_BSU_29100 + RNA_BSU_29110 + 783.434859243 mRNA_biomass + 2455 ppi_c
1814
transcription_TU8J2_2968_from_RpoD_mono
744 atp_c + 873 ctp_c + 718 gtp_c + 951 utp_c --> RNA_BSU_32240 + RNA_BSU_32250 + RNA_BSU_32260 + 1048.6094999309998 mRNA_biomass + 3286 ppi_c
1815
transcription_TU8J2_129_from_RpoD_mono
480 atp_c + 440 ctp_c + 451 gtp_c + 563 utp_c --> RNA_BSU_10670 + RNA_BSU_10680 + RNA_BSU_10690 + RNA_BSU_10700 + RNA_BSU_10710 + RNA_BSU_10720 + 598.87234589

0.000498399634202103*mu + 0.000195123456790123 + 0.00598079561042524*(mu + 0.3915)/mu RNA_BSU_00160 + 1.9183401920439*(mu + 0.3915)/mu atp_c + 1.9183401920439*(mu + 0.3915)/mu h2o_c + 2.45552708331172*(mu + 0.3915)/mu mRNA_biomass + met__L_c --> 1.9183401920439*(mu + 0.3915)/mu adp_c + 1.8480658436214*(mu + 0.3915)/mu amp_c + 1.70452674897119*(mu + 0.3915)/mu cmp_c + 1.8241426611797*(mu + 0.3915)/mu gmp_c + 1.9183401920439*(mu + 0.3915)/mu h_c + 1.9183401920439*(mu + 0.3915)/mu pi_c + protein_BSU_00160 + 0.14921134 protein_biomass + 2.30260631001372*(mu + 0.3915)/mu ump_c
1874
translation_BSU_00170
0.000498399634202103*mu + 0.000195123456790123 + 0.00598079561042524*(mu + 0.3915)/mu RNA_BSU_00170 + 0.814883401920439*(mu + 0.3915)/mu atp_c + 0.814883401920439*(mu + 0.3915)/mu h2o_c + met__L_c --> 0.814883401920439*(mu + 0.3915)/mu adp_c + 0.843292181069959*(mu + 0.3915)/mu amp_c + 0.604060356652949*(mu + 0.3915)/mu cmp_c + 0.62798353909465*(mu + 0.3915)/mu gmp_c + 0.814883401920439*(mu 

...

RNA_BSU_28740 + 302.077832682 mRNA_biomass --> 
9610
DM_RNA_BSU_28770
RNA_BSU_28770 + 260.545295039 mRNA_biomass --> 
9611
DM_RNA_BSU_22300
RNA_BSU_22300 + 307.52498468299996 mRNA_biomass --> 
9612
DM_RNA_BSU_24790
RNA_BSU_24790 + 202.697566116 mRNA_biomass --> 
9613
DM_RNA_BSU_07640
RNA_BSU_07640 + 88.199053316 mRNA_biomass --> 
9614
DM_RNA_BSU_03070
RNA_BSU_03070 + 493.46396197900003 mRNA_biomass --> 
9615
DM_RNA_BSU_37570
RNA_BSU_37570 + 449.702291281 mRNA_biomass --> 
9616
DM_RNA_BSU_37290
RNA_BSU_37290 + 153.094141097 mRNA_biomass --> 
9617
DM_RNA_BSU_32010
RNA_BSU_32010 + 278.00706189 mRNA_biomass --> 
9618
DM_RNA_BSU_10470
RNA_BSU_10470 + 115.670034963 mRNA_biomass --> 
9619
DM_RNA_BSU_24570
RNA_BSU_24570 + 346.223250509 mRNA_biomass --> 
9620
DM_RNA_BSU_24560
RNA_BSU_24560 + 429.583227747 mRNA_biomass --> 
9621
DM_RNA_BSU_24550
RNA_BSU_24550 + 467.53701578700003 mRNA_biomass --> 
9622
DM_RNA_BSU_24210
RNA_BSU_24210 + 356.987116099 mRNA_biomass --> 
9623
DM_RNA_BSU_17840
RNA_BSU

RNA_BSU_36310 + 109.11766350200001 mRNA_biomass --> 
10202
DM_RNA_BSU_41030
RNA_BSU_41030 + 199.00169100699998 mRNA_biomass --> 
10203
DM_RNA_BSU_41040
RNA_BSU_41040 + 250.567801026 mRNA_biomass --> 
10204
DM_RNA_BSU_22770
RNA_BSU_22770 + 72.23834978800001 mRNA_biomass --> 
10205
DM_RNA_BSU_22780
RNA_BSU_22780 + 182.32165361299997 mRNA_biomass --> 
10206
DM_RNA_BSU_06460
RNA_BSU_06460 + 80.804410075 mRNA_biomass --> 
10207
DM_RNA_BSU_06430
RNA_BSU_06430 + 363.353579883 mRNA_biomass --> 
10208
DM_RNA_BSU_06530
RNA_BSU_06530 + 403.730064569 mRNA_biomass --> 
10209
DM_RNA_BSU_06480
RNA_BSU_06480 + 710.389030789 mRNA_biomass --> 
10210
DM_RNA_BSU_06510
RNA_BSU_06510 + 187.381724908 mRNA_biomass --> 
10211
DM_RNA_BSU_06520
RNA_BSU_06520 + 490.693158219 mRNA_biomass --> 
10212
DM_RNA_BSU_06440
RNA_BSU_06440 + 413.373238776 mRNA_biomass --> 
10213
DM_RNA_BSU_06420
RNA_BSU_06420 + 155.86593436899997 mRNA_biomass --> 
10214
DM_RNA_BSU_06500
RNA_BSU_06500 + 331.44051906100003 mRNA_biomass --> 
1

10776
DM_RNA_BSU_00650
RNA_BSU_00650 + 234.557161838 mRNA_biomass --> 
10777
DM_RNA_BSU_00660
RNA_BSU_00660 + 323.682278457 mRNA_biomass --> 
10778
DM_RNA_BSU_00670
RNA_BSU_00670 + 451.713381479 mRNA_biomass --> 
10779
DM_RNA_BSU_00680
RNA_BSU_00680 + 172.46431244299998 mRNA_biomass --> 
10780
DM_RNA_BSU_00700
RNA_BSU_00700 + 247.34053883699997 mRNA_biomass --> 
10781
DM_RNA_BSU_00710
RNA_BSU_00710 + 278.446873516 mRNA_biomass --> 
10782
DM_RNA_BSU_00720
RNA_BSU_00720 + 283.286882194 mRNA_biomass --> 
10783
DM_RNA_BSU_rRNA_9
RNA_BSU_rRNA_9 + 495.241019354 rRNA_biomass --> 
10784
DM_RNA_BSU_rRNA_10
RNA_BSU_rRNA_10 + 931.440514868 rRNA_biomass --> 
10785
DM_RNA_BSU_rRNA_11
RNA_BSU_rRNA_11 + 38.056550639 rRNA_biomass --> 
10786
DM_RNA_BSU_00990
RNA_BSU_00990 + 47.53452185 mRNA_biomass --> 
10787
DM_RNA_BSU_01000
RNA_BSU_01000 + 57.30843898 mRNA_biomass --> 
10788
DM_RNA_BSU_01010
RNA_BSU_01010 + 169.22715783400002 mRNA_biomass --> 
10789
DM_RNA_BSU_01020
RNA_BSU_01020 + 135.728555346 mRNA

DM_RNA_BSU_16130
RNA_BSU_16130 + 416.204233768 mRNA_biomass --> 
11443
DM_RNA_BSU_16490
RNA_BSU_16490 + 235.90330856100002 mRNA_biomass --> 
11444
DM_RNA_BSU_16500
RNA_BSU_16500 + 280.340098622 mRNA_biomass --> 
11445
DM_RNA_BSU_16510
RNA_BSU_16510 + 229.87045496300001 mRNA_biomass --> 
11446
DM_RNA_BSU_16520
RNA_BSU_16520 + 176.90496519799999 mRNA_biomass --> 
11447
DM_RNA_BSU_16530
RNA_BSU_16530 + 249.016461823 mRNA_biomass --> 
11448
DM_RNA_BSU_16540
RNA_BSU_16540 + 259.33523263 mRNA_biomass --> 
11449
DM_RNA_BSU_16550
RNA_BSU_16550 + 366.924036372 mRNA_biomass --> 
11450
DM_RNA_BSU_16560
RNA_BSU_16560 + 404.22450518899996 mRNA_biomass --> 
11451
DM_RNA_BSU_16570
RNA_BSU_16570 + 539.6768244950001 mRNA_biomass --> 
11452
DM_RNA_BSU_16580
RNA_BSU_16580 + 1374.224402034 mRNA_biomass --> 
11453
DM_RNA_BSU_16660
RNA_BSU_16660 + 295.81110605 mRNA_biomass --> 
11454
DM_RNA_BSU_16670
RNA_BSU_16670 + 302.44830325099997 mRNA_biomass --> 
11455
DM_RNA_BSU_16680
RNA_BSU_16680 + 86.35757245 mRNA

12109
DM_RNA_BSU_29440
RNA_BSU_29440 + 441.191613586 mRNA_biomass --> 
12110
DM_RNA_BSU_29450
RNA_BSU_29450 + 386.203531012 mRNA_biomass --> 
12111
DM_RNA_BSU_29479
RNA_BSU_29479 + 64.710355944 mRNA_biomass --> 
12112
DM_RNA_BSU_29560
RNA_BSU_29560 + 506.02638409 mRNA_biomass --> 
12113
DM_RNA_BSU_29580
RNA_BSU_29580 + 384.02493076599995 mRNA_biomass --> 
12114
DM_RNA_BSU_29590
RNA_BSU_29590 + 365.21295550599996 mRNA_biomass --> 
12115
DM_RNA_BSU_29805
RNA_BSU_29805 + 910.7292647790001 mRNA_biomass --> 
12116
DM_RNA_BSU_29845
RNA_BSU_29845 + 37.134910937 mRNA_biomass --> 
12117
DM_RNA_BSU_29890
RNA_BSU_29890 + 245.553297611 mRNA_biomass --> 
12118
DM_RNA_BSU_29920
RNA_BSU_29920 + 195.923709295 mRNA_biomass --> 
12119
DM_RNA_BSU_29940
RNA_BSU_29940 + 297.10124028999996 mRNA_biomass --> 
12120
DM_RNA_BSU_29950
RNA_BSU_29950 + 291.174073415 mRNA_biomass --> 
12121
DM_RNA_BSU_29960
RNA_BSU_29960 + 176.07323869200002 mRNA_biomass --> 
12122
DM_RNA_BSU_30035
RNA_BSU_30035 + 229.09798424 mRNA

### 4) Add in complex Formation without modifications (for now)

The below reads in:
- Required
 * **protein_complexes.txt** (Metabolic complexes' protein subunit stoichiometries)
 * **protein_modification.txt** (Type and number of modifications for each protein)

In [9]:
# complex_stoichiometry_dict is a dict of {'complex_id': [{'bnum' : count}]}
rna_components = {} # component id should have 'RNA_ instead' of 'protein_'
# get Metabolic Complex composition from ECOLIme
complex_stoichiometry_dict = flat_files.get_complex_subunit_stoichiometry('protein_complexes.txt', rna_components)
# add complexes to model
complex_modification_dict = flat_files.get_complex_modifications('protein_modification.txt', 'protein_complexes.txt')
building.add_model_complexes(me, complex_stoichiometry_dict, complex_modification_dict, verbose=False)

# remove modifications. they will be added back in later
for data in me.complex_data:
    data.subreactions = {}
    
# add formation reactions for each of the ComplexDatas
for cplx_data in me.complex_data:
    formation = cplx_data.formation
    if formation:
        formation.update()
    else:
        cplx_data.create_complex_formation()

Created <TranslatedGene protein_BSU32760 at 0x7f3883d2b128> in <ComplexFormation formation_BSU32760-MONOMER at 0x7f3883d2b208>
Created <TranslatedGene protein_BSU37060 at 0x7f3883d2b2e8> in <ComplexFormation formation_BSU37060-MONOMER at 0x7f3883d2b198>
Created <TranslatedGene protein_BSU36370 at 0x7f3884039fd0> in <ComplexFormation formation_BSU36370-MONOMER at 0x7f3883d2b080>
Created <TranslatedGene protein_BSU14440 at 0x7f3884039e80> in <ComplexFormation formation_BSU14440-MONOMER at 0x7f3884039860>
Created <TranslatedGene protein_BSU13790 at 0x7f3884039f28> in <ComplexFormation formation_BSU13790-MONOMER at 0x7f38840390f0>
Created <TranslatedGene protein_BSU18070 at 0x7f3884039908> in <ComplexFormation formation_BSU18070-MONOMER at 0x7f3884039780>
Created <TranslatedGene protein_BSU17410 at 0x7f38840392b0> in <ComplexFormation formation_BSU17410-MONOMER at 0x7f3884039f60>
Created <TranslatedGene protein_BSU40670 at 0x7f3884039eb8> in <ComplexFormation formation_BSU40670-MONOMER at 

Created <TranslatedGene protein_BSU39990 at 0x7f3883718780> in <ComplexFormation formation_CPLX8J2-112 at 0x7f3883718828>
Created <TranslatedGene protein_BSU00730 at 0x7f3883718748> in <ComplexFormation formation_BSU00730-MONOMER at 0x7f38837182b0>
Created <TranslatedGene protein_BSU07630 at 0x7f3883718d68> in <ComplexFormation formation_CPLX-9195 at 0x7f3883718dd8>
Created <TranslatedGene protein_BSU15930 at 0x7f3883718be0> in <ComplexFormation formation_BSU15930-MONOMER at 0x7f3883718d30>
Created <TranslatedGene protein_BSU03290 at 0x7f388371b5f8> in <ComplexFormation formation_CPLX8J2-87 at 0x7f3883718c88>
Created <TranslatedGene protein_BSU03300 at 0x7f388371b5c0> in <ComplexFormation formation_CPLX8J2-87 at 0x7f3883718c88>
Created <TranslatedGene protein_BSU11430 at 0x7f388371b8d0> in <ComplexFormation formation_CPLX8J2-72 at 0x7f388371b4e0>
Created <TranslatedGene protein_BSU11440 at 0x7f388371b3c8> in <ComplexFormation formation_CPLX8J2-72 at 0x7f388371b4e0>
Created <TranslatedG

Created <TranslatedGene protein_BSU04250 at 0x7f388367ac88> in <ComplexFormation formation_BSU04250-MONOMER at 0x7f388367ae80>
Created <TranslatedGene protein_BSU31650 at 0x7f38836814a8> in <ComplexFormation formation_CPLX8J2-158 at 0x7f388367ac18>
Created <TranslatedGene protein_BSU31640 at 0x7f3883681390> in <ComplexFormation formation_CPLX8J2-158 at 0x7f388367ac18>
Created <TranslatedGene protein_BSU31620 at 0x7f3883681400> in <ComplexFormation formation_CPLX8J2-158 at 0x7f388367ac18>
Created <TranslatedGene protein_BSU31610 at 0x7f3883681438> in <ComplexFormation formation_CPLX8J2-158 at 0x7f388367ac18>
Created <TranslatedGene protein_BSU31600 at 0x7f388367ab70> in <ComplexFormation formation_CPLX8J2-158 at 0x7f388367ac18>
Created <TranslatedGene protein_BSU10840 at 0x7f38836817b8> in <ComplexFormation formation_BSU10840-MONOMER at 0x7f3883681470>
Created <TranslatedGene protein_BSU14580 at 0x7f3883681940> in <ComplexFormation formation_CPLX8J2-13 at 0x7f3883681320>
Created <Transl

Created <TranslatedGene protein_BSU05290 at 0x7f3883592240> in <ComplexFormation formation_BSU05290-MONOMER at 0x7f3883592588>
Created <TranslatedGene protein_BSU31210 at 0x7f3883592fd0> in <ComplexFormation formation_CPLX8J2-160 at 0x7f3883592ef0>
Created <TranslatedGene protein_BSU35920 at 0x7f3883592cf8> in <ComplexFormation formation_BSU35920-MONOMER at 0x7f3883592da0>
Created <TranslatedGene protein_BSU08900 at 0x7f3883518748> in <ComplexFormation formation_BSU08900-MONOMER at 0x7f38835180f0>
Created <TranslatedGene protein_BSU22770 at 0x7f3883518358> in <ComplexFormation formation_CPLX8J2-63 at 0x7f3883518668>
Created <TranslatedGene protein_BSU03230 at 0x7f3883518e10> in <ComplexFormation formation_CPLX8J2-115 at 0x7f3883518f98>
Created <TranslatedGene protein_BSU27810 at 0x7f388351d160> in <ComplexFormation formation_BSU27810-MONOMER at 0x7f3883518c50>
Created <TranslatedGene protein_BSU20450 at 0x7f388351d940> in <ComplexFormation formation_BSU20450-MONOMER at 0x7f388351d080>


Created <TranslatedGene protein_BSU19600 at 0x7f388338ff60> in <ComplexFormation formation_BSU19600-MONOMER at 0x7f388338fda0>
Created <TranslatedGene protein_BSU28460 at 0x7f38833160f0> in <ComplexFormation formation_BSU28460-MONOMER at 0x7f388338fcf8>
Created <TranslatedGene protein_BSU01490 at 0x7f3883316048> in <ComplexFormation formation_BSU01490-MONOMER at 0x7f38833160b8>
Created <TranslatedGene protein_BSU38630 at 0x7f38833165f8> in <ComplexFormation formation_BSU38630-MONOMER at 0x7f38833167b8>
Created <TranslatedGene protein_BSU13140 at 0x7f3883316a20> in <ComplexFormation formation_BSU13140-MONOMER at 0x7f3883316518>
Created <TranslatedGene protein_BSU19579 at 0x7f3883316da0> in <ComplexFormation formation_BSU19579-MONOMER at 0x7f38833164e0>
Created <TranslatedGene protein_BSU16690 at 0x7f3883316b00> in <ComplexFormation formation_BSU16690-MONOMER at 0x7f3883316d68>
Created <TranslatedGene protein_BSU01460 at 0x7f3883316ac8> in <ComplexFormation formation_BSU01460-MONOMER at 

Created <TranslatedGene protein_BSU06890 at 0x7f388318aeb8> in <ComplexFormation formation_BSU06890-MONOMER at 0x7f388318af28>
Created <TranslatedGene protein_BSU21920 at 0x7f388318ab70> in <ComplexFormation formation_BSU21920-MONOMER at 0x7f388367a4a8>
Created <TranslatedGene protein_BSU10590 at 0x7f388318e6d8> in <ComplexFormation formation_BSU10590-MONOMER at 0x7f388318add8>
Created <TranslatedGene protein_BSU28550 at 0x7f388318e630> in <ComplexFormation formation_BSU28550-MONOMER at 0x7f388318e6a0>
Created <TranslatedGene protein_BSU21160 at 0x7f388318eb00> in <ComplexFormation formation_BSU21160-MONOMER at 0x7f388318e860>
Created <TranslatedGene protein_BSU36700 at 0x7f388318ea58> in <ComplexFormation formation_BSU36700-MONOMER at 0x7f388318eac8>
Created <TranslatedGene protein_BSU32190 at 0x7f388318ee10> in <ComplexFormation formation_BSU32190-MONOMER at 0x7f388318e9e8>
Created <TranslatedGene protein_BSU14080 at 0x7f388318ef28> in <ComplexFormation formation_BSU14080-MONOMER at 

Created <TranslatedGene protein_BSU23310 at 0x7f3882f905c0> in <ComplexFormation formation_BSU23310-MONOMER at 0x7f3882f90668>
Created <TranslatedGene protein_BSU02540 at 0x7f3882f90f28> in <ComplexFormation formation_BSU02540-MONOMER at 0x7f3882f90b00>
Created <TranslatedGene protein_BSU04480 at 0x7f3882f90be0> in <ComplexFormation formation_BSU04480-MONOMER at 0x7f3882f90c88>
Created <TranslatedGene protein_BSU06110 at 0x7f3882f168d0> in <ComplexFormation formation_BSU06110-MONOMER at 0x7f3882f90b70>
Created <TranslatedGene protein_BSU09760 at 0x7f3882f16a20> in <ComplexFormation formation_BSU09760-MONOMER at 0x7f3882f16b00>
Created <TranslatedGene protein_BSU28650 at 0x7f3882f1a668> in <ComplexFormation formation_BSU28650-MONOMER at 0x7f3882f16940>
Created <TranslatedGene protein_BSU32290 at 0x7f3882f1a400> in <ComplexFormation formation_BSU32290-MONOMER at 0x7f3882f1a550>
Created <TranslatedGene protein_BSU27000 at 0x7f3882f1a7f0> in <ComplexFormation formation_BSU27000-MONOMER at 

Created <TranslatedGene protein_BSU24470 at 0x7f3882d28668> in <ComplexFormation formation_BSU24470-MONOMER at 0x7f3882d28748>
Created <TranslatedGene protein_BSU08530 at 0x7f3882d284a8> in <ComplexFormation formation_BSU08530-MONOMER at 0x7f3882d28630>
Created <TranslatedGene protein_BSU05580 at 0x7f3882d28da0> in <ComplexFormation formation_BSU05580-MONOMER at 0x7f3882d28e48>
Created <TranslatedGene protein_BSU09240 at 0x7f3882d2e358> in <ComplexFormation formation_BSU09240-MONOMER at 0x7f3882d2e3c8>
Created <TranslatedGene protein_BSU31080 at 0x7f3882d2e710> in <ComplexFormation formation_BSU31080-MONOMER at 0x7f3882d2e320>
Created <TranslatedGene protein_BSU28130 at 0x7f3882d2e8d0> in <ComplexFormation formation_BSU28130-MONOMER at 0x7f3882d2ea90>
Created <TranslatedGene protein_BSU12160 at 0x7f3882d2ec50> in <ComplexFormation formation_BSU12160-MONOMER at 0x7f3882d2e828>
Created <TranslatedGene protein_BSU31770 at 0x7f3882d2ee48> in <ComplexFormation formation_BSU31770-MONOMER at 

Created <TranslatedGene protein_BSU15450 at 0x7f3882b206a0> in <ComplexFormation formation_BSU15450-MONOMER at 0x7f3882b20080>
Created <TranslatedGene protein_BSU16180 at 0x7f3882b20630> in <ComplexFormation formation_BSU16180-MONOMER at 0x7f3882b206d8>
Created <TranslatedGene protein_BSU34490 at 0x7f3882b205c0> in <ComplexFormation formation_BSU34490-MONOMER at 0x7f3882b20518>
Created <TranslatedGene protein_BSU35200 at 0x7f3882b20ba8> in <ComplexFormation formation_BSU35200-MONOMER at 0x7f3882b20c18>
Created <TranslatedGene protein_BSU38130 at 0x7f3882b205f8> in <ComplexFormation formation_BSU38130-MONOMER at 0x7f3882b20b70>
Created <TranslatedGene protein_BSU38830 at 0x7f3882b2b048> in <ComplexFormation formation_BSU38830-MONOMER at 0x7f3882b20940>
Created <TranslatedGene protein_BSU19070 at 0x7f3882b2b198> in <ComplexFormation formation_BSU19070-MONOMER at 0x7f3882b2b208>
Created <TranslatedGene protein_BSU19740 at 0x7f3882b2b4e0> in <ComplexFormation formation_BSU19740-MONOMER at 

In [10]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

12453
formation_BSU32760-MONOMER
protein_BSU32760 --> BSU32760-MONOMER
12454
formation_BSU37060-MONOMER
protein_BSU37060 --> BSU37060-MONOMER
12455
formation_BSU36370-MONOMER
protein_BSU36370 --> BSU36370-MONOMER
12456
formation_BSU14440-MONOMER
protein_BSU14440 --> BSU14440-MONOMER
12457
formation_BSU13790-MONOMER
protein_BSU13790 --> BSU13790-MONOMER
12458
formation_BSU18070-MONOMER
protein_BSU18070 --> BSU18070-MONOMER
12459
formation_BSU17410-MONOMER
protein_BSU17410 --> BSU17410-MONOMER
12460
formation_BSU40670-MONOMER
protein_BSU40670 --> BSU40670-MONOMER
12461
formation_BSU40022-MONOMER
protein_BSU40022 --> BSU40022-MONOMER
12462
formation_BSU22340-MONOMER
protein_BSU22340 --> BSU22340-MONOMER
12463
formation_BSU20929-MONOMER
protein_BSU20929 --> BSU20929-MONOMER
12464
formation_BSU21580-MONOMER
protein_BSU21580 --> BSU21580-MONOMER
12465
formation_BSU02870-MONOMER
protein_BSU02870 --> BSU02870-MONOMER
12466
formation_BSU03550-MONOMER
protein_BSU03550 --> BSU03550-MONOMER
12467


protein_BSU20590 --> BSU20590-MONOMER
13038
formation_BSU40330-MONOMER
protein_BSU40330 --> BSU40330-MONOMER
13039
formation_BSU02530-MONOMER
protein_BSU02530 --> BSU02530-MONOMER
13040
formation_BSU22010-MONOMER
protein_BSU22010 --> BSU22010-MONOMER
13041
formation_BSU24970-MONOMER
protein_BSU24970 --> BSU24970-MONOMER
13042
formation_BSU21240-MONOMER
protein_BSU21240 --> BSU21240-MONOMER
13043
formation_BSU06100-MONOMER
protein_BSU06100 --> BSU06100-MONOMER
13044
formation_BSU03210-MONOMER
protein_BSU03210 --> BSU03210-MONOMER
13045
formation_BSU09750-MONOMER
protein_BSU09750 --> BSU09750-MONOMER
13046
formation_BSU25640-MONOMER
protein_BSU25640 --> BSU25640-MONOMER
13047
formation_BSU28640-MONOMER
protein_BSU28640 --> BSU28640-MONOMER
13048
formation_BSU29290-MONOMER
protein_BSU29290 --> BSU29290-MONOMER
13049
formation_BSU32280-MONOMER
protein_BSU32280 --> BSU32280-MONOMER
13050
formation_BSU06760-MONOMER
protein_BSU06760 --> BSU06760-MONOMER
13051
formation_BSU13300-MONOMER
protei

protein_BSU29850 --> BSU29850-MONOMER
13538
formation_CPLX8J2-32
protein_BSU27730 + protein_BSU27740 --> CPLX8J2-32
13539
formation_BSU23230-MONOMER
protein_BSU23230 --> BSU23230-MONOMER
13540
formation_CPLX8J2-194
protein_BSU26970 --> CPLX8J2-194
13541
formation_BSU07320-MONOMER
protein_BSU07320 --> BSU07320-MONOMER
13542
formation_CPLX8J2-179
protein_BSU32110 --> CPLX8J2-179
13543
formation_BSU04410-MONOMER
protein_BSU04410 --> BSU04410-MONOMER
13544
formation_CPLX8J2-164
protein_BSU03790 --> CPLX8J2-164
13545
formation_BSU11000-MONOMER
protein_BSU11000 --> BSU11000-MONOMER
13546
formation_CPLX8J2-14
protein_BSU00060 + protein_BSU00070 --> CPLX8J2-14
13547
formation_BSU08010-MONOMER
protein_BSU08010 --> BSU08010-MONOMER
13548
formation_CPLX8J2-119
protein_BSU34590 + protein_BSU34600 + protein_BSU34610 --> CPLX8J2-119
13549
formation_BSU33460-MONOMER
protein_BSU33460 --> BSU33460-MONOMER
13550
formation_CPLX8J2-101
protein_BSU36800 + protein_BSU36810 + protein_BSU36820 + protein_BSU36

14204
formation_BSU29200-MONOMER
protein_BSU29200 --> BSU29200-MONOMER
14205
formation_BSU03780-MONOMER
protein_BSU03780 --> BSU03780-MONOMER
14206
formation_BSU06650-MONOMER
protein_BSU06650 --> BSU06650-MONOMER
14207
formation_BSU26240-MONOMER
protein_BSU26240 --> BSU26240-MONOMER
14208
formation_BSU10330-MONOMER
protein_BSU10330 --> BSU10330-MONOMER
14209
formation_BSU29870-MONOMER
protein_BSU29870 --> BSU29870-MONOMER
14210
formation_BSU32830-MONOMER
protein_BSU32830 --> BSU32830-MONOMER
14211
formation_BSU07340-MONOMER
protein_BSU07340 --> BSU07340-MONOMER
14212
formation_BSU36440-MONOMER
protein_BSU36440 --> BSU36440-MONOMER
14213
formation_BSU11020-MONOMER
protein_BSU11020 --> BSU11020-MONOMER
14214
formation_BSU13840-MONOMER
protein_BSU13840 --> BSU13840-MONOMER
14215
formation_BSU33480-MONOMER
protein_BSU33480 --> BSU33480-MONOMER
14216
formation_BSU17480-MONOMER
protein_BSU17480 --> BSU17480-MONOMER
14217
formation_BSU37130-MONOMER
protein_BSU37130 --> BSU37130-MONOMER
14218


14704
formation_BSU23880-MONOMER
protein_BSU23880 --> BSU23880-MONOMER
14705
formation_BSU30180-MONOMER
protein_BSU30180 --> BSU30180-MONOMER
14706
formation_BSU05060-MONOMER
protein_BSU05060 --> BSU05060-MONOMER
14707
formation_BSU14110-MONOMER
protein_BSU14110 --> BSU14110-MONOMER
14708
formation_BSU08670-MONOMER
protein_BSU08670 --> BSU08670-MONOMER
14709
formation_BSU11300-MONOMER
protein_BSU11300 --> BSU11300-MONOMER
14710
formation_BSU27570-MONOMER
protein_BSU27570 --> BSU27570-MONOMER
14711
formation_BSU17750-MONOMER
protein_BSU17750 --> BSU17750-MONOMER
14712
formation_BSU31220-MONOMER
protein_BSU31220 --> BSU31220-MONOMER
14713
formation_BSU14750-MONOMER
protein_BSU14750 --> BSU14750-MONOMER
14714
formation_BSU12290-MONOMER
protein_BSU12290 --> BSU12290-MONOMER
14715
formation_BSU40350-MONOMER
protein_BSU40350 --> BSU40350-MONOMER
14716
formation_BSU15780-MONOMER
protein_BSU15780 --> BSU15780-MONOMER
14717
formation_BSU33770-MONOMER
protein_BSU33770 --> BSU33770-MONOMER
14718


protein_BSU35000 --> BSU35000-MONOMER
15204
formation_BSU19680-MONOMER
protein_BSU19680 --> BSU19680-MONOMER
15205
formation_BSU09540-MONOMER
protein_BSU09540 --> BSU09540-MONOMER
15206
formation_BSU01590-MONOMER
protein_BSU01590 --> BSU01590-MONOMER
15207
formation_BSU24040-MONOMER
protein_BSU24040 --> BSU24040-MONOMER
15208
formation_BSU28430-MONOMER
protein_BSU28430 --> BSU28430-MONOMER
15209
formation_BSU05200-MONOMER
protein_BSU05200 --> BSU05200-MONOMER
15210
formation_BSU08820-MONOMER
protein_BSU08820 --> BSU08820-MONOMER
15211
formation_BSU32080-MONOMER
protein_BSU32080 --> BSU32080-MONOMER
15212
formation_BSU27729-MONOMER
protein_BSU27729 --> BSU27729-MONOMER
15213
formation_BSU31350-MONOMER
protein_BSU31350 --> BSU31350-MONOMER
15214
formation_BSU13110-MONOMER
protein_BSU13110 --> BSU13110-MONOMER
15215
formation_BSU27700-MONOMER
protein_BSU27700 --> BSU27700-MONOMER
15216
formation_BSU31322-MONOMER
protein_BSU31322 --> BSU31322-MONOMER
15217
formation_BSU16660-MONOMER
protei

formation_BSU33950-MONOMER
protein_BSU33950 --> BSU33950-MONOMER
15725
formation_BSU40529-MONOMER
protein_BSU40529 --> BSU40529-MONOMER
15726
formation_BSU00210-MONOMER
protein_BSU00210 --> BSU00210-MONOMER
15727
formation_BSU22190-MONOMER
protein_BSU22190 --> BSU22190-MONOMER
15728
formation_BSU37600-MONOMER
protein_BSU37600 --> BSU37600-MONOMER
15729
formation_BSU21430-MONOMER
protein_BSU21430 --> BSU21430-MONOMER
15730
formation_BSU18600-MONOMER
protein_BSU18600 --> BSU18600-MONOMER
15731
formation_BSU03400-MONOMER
protein_BSU03400 --> BSU03400-MONOMER
15732
formation_BSU22869-MONOMER
protein_BSU22869 --> BSU22869-MONOMER
15733
formation_BSU25850-MONOMER
protein_BSU25850 --> BSU25850-MONOMER
15734
formation_BSU04050-MONOMER
protein_BSU04050 --> BSU04050-MONOMER
15735
formation_BSU29490-MONOMER
protein_BSU29490 --> BSU29490-MONOMER
15736
formation_BSU07630-MONOMER
protein_BSU07630 --> BSU07630-MONOMER
15737
formation_BSU06940-MONOMER
protein_BSU06940 --> BSU06940-MONOMER
15738
format

16270
formation_BSU00550-MONOMER
protein_BSU00550 --> BSU00550-MONOMER
16271
formation_BSU21560-MONOMER
protein_BSU21560 --> BSU21560-MONOMER
16272
formation_BSU22990-MONOMER
protein_BSU22990 --> BSU22990-MONOMER
16273
formation_BSU03530-MONOMER
protein_BSU03530 --> BSU03530-MONOMER
16274
formation_BSU04180-MONOMER
protein_BSU04180 --> BSU04180-MONOMER
16275
formation_BSU25980-MONOMER
protein_BSU25980 --> BSU25980-MONOMER
16276
formation_BSU07770-MONOMER
protein_BSU07770 --> BSU07770-MONOMER
16277
formation_BSU29620-MONOMER
protein_BSU29620 --> BSU29620-MONOMER
16278
formation_BSU26690-MONOMER
protein_BSU26690 --> BSU26690-MONOMER
16279
formation_BSU07070-MONOMER
protein_BSU07070 --> BSU07070-MONOMER
16280
formation_BSU30330-MONOMER
protein_BSU30330 --> BSU30330-MONOMER
16281
formation_BSU10770-MONOMER
protein_BSU10770 --> BSU10770-MONOMER
16282
formation_BSU11460-MONOMER
protein_BSU11460 --> BSU11460-MONOMER
16283
formation_BSU33239-MONOMER
protein_BSU33239 --> BSU33239-MONOMER
16284


16870
formation_BSU03710-MONOMER
protein_BSU03710 --> BSU03710-MONOMER
16871
formation_BSU03030-MONOMER
protein_BSU03030 --> BSU03030-MONOMER
16872
formation_BSU26170-MONOMER
protein_BSU26170 --> BSU26170-MONOMER
16873
formation_BSU25470-MONOMER
protein_BSU25470 --> BSU25470-MONOMER
16874
formation_BSU29790-MONOMER
protein_BSU29790 --> BSU29790-MONOMER
16875
formation_BSU29130-MONOMER
protein_BSU29130 --> BSU29130-MONOMER
16876
formation_BSU07270-MONOMER
protein_BSU07270 --> BSU07270-MONOMER
16877
formation_BSU06580-MONOMER
protein_BSU06580 --> BSU06580-MONOMER
16878
formation_BSU10950-MONOMER
protein_BSU10950 --> BSU10950-MONOMER
16879
formation_BSU10260-MONOMER
protein_BSU10260 --> BSU10260-MONOMER
16880
formation_BSU33410-MONOMER
protein_BSU33410 --> BSU33410-MONOMER
16881
formation_CPLX000-1
protein_BSU07700 + protein_BSU13900 + protein_BSU13910 --> CPLX000-1
16882
formation_CPLX000-2
protein_BSU30410 + protein_BSU30420 + protein_BSU30430 + protein_BSU30440 + protein_BSU30450 --> C

### 5) Add dummy reaction to model and unmodeled_protein_fraction

Includes the transcription, translation, complex_formation, and metabolic reaction. Sequence based on prevelance of each codon found in *E. coli*.
 - Required
     * [**codon_usage.csv**](http://openwetware.org/wiki/Escherichia_coli/Codon_usage) (codon prevelance)

In [11]:
seq = "ATG"
codons = pandas.read_csv(join(flat_files.ecoli_files_dir, "codon_usage.csv"), index_col=0)
for codon, row in codons.iterrows():
    if row.amino_acid == "Stop":
        continue
    seq += codon * int(row.per_1000 // 3)  # want roughly 300 aa
# get the most used stop codon
seq += codons[codons.amino_acid == "Stop"].sort_values("per_1000").index[-1]
building.add_dummy_reactions(me, seq, update=True)

# dummy proteins can be used to catalyze orphan reactions. This
# ensures that orphan reactions will not becore favored to fulfil 
# unmodeled protein fraction requirement 
rxn = cobrame.SummaryVariable('dummy_protein_to_mass')
me.add_reactions([rxn])
mass = me.metabolites.protein_dummy.formula_weight / 1000.  # in kDa
rxn.add_metabolites({'protein_biomass': -mass, 'protein_dummy': -1,
                     cobrame.Constraint('unmodeled_protein_biomass'): mass})

In [12]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

17069
transcription_RNA_dummy
220 atp_c + 250 ctp_c + 220 gtp_c + 222 utp_c --> RNA_dummy + 291.715403232 mRNA_biomass + 912 ppi_c
17070
DM_RNA_dummy
RNA_dummy + 291.715403232 mRNA_biomass --> 
17071
translation_dummy
0.000498399634202103*mu + 0.000195123456790123 + 0.00598079561042524*(mu + 0.3915)/mu RNA_dummy + 1.36212620027435*(mu + 0.3915)/mu atp_c + 1.36212620027435*(mu + 0.3915)/mu h2o_c + 1.74469020314338*(mu + 0.3915)/mu mRNA_biomass + met__L_c --> 1.36212620027435*(mu + 0.3915)/mu adp_c + 1.31577503429355*(mu + 0.3915)/mu amp_c + 1.49519890260631*(mu + 0.3915)/mu cmp_c + 1.31577503429355*(mu + 0.3915)/mu gmp_c + 1.36212620027435*(mu + 0.3915)/mu h_c + 1.36212620027435*(mu + 0.3915)/mu pi_c + 0.14921134 protein_biomass + protein_dummy + 1.3277366255144*(mu + 0.3915)/mu ump_c
17072
formation_CPLX_dummy
protein_dummy --> CPLX_dummy
17073
dummy_protein_to_mass
0.14921134 protein_biomass + protein_dummy --> 0.14921134 unmodeled_protein_biomass


### 6) Assocated Complexes and build Metabolic Reactions 
- Required
    * **enzyme_reaction_association.txt**
    * **reactions.txt** (gives reaction name, reversiblity, source and whether reaction is spontaneous)


In [13]:
# associate reaction id with the old ME complex id (including modifications)
rxn_to_cplx_dict = flat_files.get_reaction_to_complex(m_model)
rxn_info = flat_files.get_reaction_info_frame('reactions.txt')

# Required to add dummy reaction as spontaneous reaction
rxn_info = rxn_info.append(pandas.Series({'description': 'dummy reaction', 'is_reversible': 0,
                                          'is_spontaneous':1}, name='dummy_reaction'))

building.add_reactions_from_stoichiometric_data(me, rxn_to_cplx_dict, rxn_info, update=True)

In [14]:
rxn_info

description  \
#name                                                               
23CN2P1         2__3__cyclic_nucleotide_2__phosphodiesterase__...   
23CN2P2         2__3__cyclic_nucleotide_2__phosphodiesterase__...   
23CN2P3         2__3__cyclic_nucleotide_2__phosphodiesterase__...   
23CN2P4         2__3__cyclic_nucleotide_2__phosphodiesterase__...   
26DPAi                                      Dipicolinate_synthase   
2HXMPt6         2__hydroxymethyl_phenol_transport_inout_via_pr...   
2PGLYCt6        2_Phosphoglycolate_transport_inout_via_proton_...   
2PGt6           D_Glycerate_2_phosphate_transport_inout_via_pr...   
2S6HCCi         2_succinyl_6_hydroxy_2_4_cyclohexadiene_1_carb...   
3AMBAt2           3_aminobutyrate_transport_in_via_proton_symport   
3AMPt6                  3__AMP_transport_inout_via_proton_symport   
3CMPt6                     3__CMP_transport_in_via_proton_symport   
3GMPt6          Guanosine_3__phsophate_transport_inout_via_pro...   
3NUCLE1                                  3__nucleotidase__3__AMP_   
3NUCLE2                                  3__nucleotidase__3__UMP_   
3NUCLE3                                  3__nucleotidase__3__cMP_   
3NUCLE4                  3__nucleotidase__guanosine_3__phosphate_   
3PGt6           3_Phospho_D_glycerate_transport_inout_via_prot...   
3UMPt6                     3__UMP_transport_in_via_proton_symport   
5MTRt2          5_Methylthio_D_ribose_transport_inout_via_prot...   
6PGCt6          6_Phospho_D_gluconate_transport_inout_via_prot...   
AAMYL_1                                             Alpha_amylase   
AB6PGH                         Arbutin_6-phosphate_glucohydrolase   
ABTA                                 4-aminobutyrate_transaminase   
ABTt_1               L_arabinitol_transport_via_passive_diffusion   
ABUTD                            Aminobutyraldehyde_dehydrogenase   
MACCOAT                               2-Methylacetyl-CoA_thiolase   
ACACT1r                            Acetyl-CoA_C-acetyltransferase   
ACACT2r           Acetyl-CoA_C-acyltransferase_(butanoyl-CoA)_(r)   
ACACT3r           Acetyl-CoA_C-acyltransferase_(hexanoyl-CoA)_(r)   
...                                                           ...   
URAt2                      Uracil_transport_in_via_proton_symport   
URCN                                                    Urocanase   
UREA                                                       Urease   
UREAt                     Urea_transport_via_facilitate_diffusion   
URIC                                                      Uricase   
UMPK                                                   UMP_kinase   
URIDK2r_copy1                             Uridylate_kinase_(dUMP)   
URIDK2r_copy2                             Uridylate_kinase_(dUMP)   
URIK1                                 Uridine_kinase__ATPUridine_   
URIK2                                Uridine_kinase_(GTP:Uridine)   
URIK3                                Uridine_kinase_(ITP:Uridine)   
URIt2                     Uridine_transport_in_via_proton_symport   
VALDHr                                       Valine_dehydrogenase   
VALTA                                         Valine_transaminase   
VALt2r           L_valine_reversible_transport_via_proton_symport   
X00002                      Lumped_reaction_for_synthesis_of_pime   
HXAND                                  Hypoxanthine_dehydrogenase   
XAND                                       Xanthine_dehydrogenase   
XANt2                    Xanthine_transport_in_via_proton_symport   
XPPT                           Xanthine_phosphoribosyltransferase   
XTSNt2                 Xanthosine_transport_in_via_proton_symport   
XYL14BASE                               Xylan_1_4_beta_xylosidase   
XYLI1                                            Xylose_isomerase   
XYLI2                                            Xylose_isomerase   
XYLK                                                 Xylulokinase   
XYLt2                    D-xylose_transport_in_via_p

In [15]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

17074
23CN2P1_REV_BSU07840-MONOMER
3amp_c + 4.27350427350427e-6*mu BSU07840-MONOMER + h_c --> 23camp_c + h2o_c
17075
23CN2P1_FWD_BSU07840-MONOMER
23camp_c + 4.27350427350427e-6*mu BSU07840-MONOMER + h2o_c --> 3amp_c + h_c
17076
23CN2P2_REV_BSU07840-MONOMER
3ump_c + 4.27350427350427e-6*mu BSU07840-MONOMER + h_c --> 23cump_c + h2o_c
17077
23CN2P2_FWD_BSU07840-MONOMER
23cump_c + 4.27350427350427e-6*mu BSU07840-MONOMER + h2o_c --> 3ump_c + h_c
17078
23CN2P3_REV_BSU07840-MONOMER
3cmp_c + 4.27350427350427e-6*mu BSU07840-MONOMER + h_c --> 23ccmp_c + h2o_c
17079
23CN2P3_FWD_BSU07840-MONOMER
23ccmp_c + 4.27350427350427e-6*mu BSU07840-MONOMER + h2o_c --> 3cmp_c + h_c
17080
23CN2P4_REV_BSU07840-MONOMER
3gmp_c + 4.27350427350427e-6*mu BSU07840-MONOMER + h_c --> 23cgmp_c + h2o_c
17081
23CN2P4_FWD_BSU07840-MONOMER
23cgmp_c + 4.27350427350427e-6*mu BSU07840-MONOMER + h2o_c --> 3gmp_c + h_c
17082
26DPAi_FWD_CPLX8J2-80
23dhdp_c + 4.27350427350427e-6*mu CPLX8J2-80 + nad_c --> DPA_c + h_c + nadh_c
17083


17526
CTPS2_FWD_BSU37150-MONOMER
4.27350427350427e-6*mu BSU37150-MONOMER + atp_c + gln__L_c + h2o_c + utp_c --> adp_c + ctp_c + glu__L_c + 2.0 h_c + pi_c
17527
CYOO3_FWD_CPLX8J2-22
4.27350427350427e-6*mu CPLX8J2-22 + 2.0 focytcc_c + 6.0 h_c + 0.5 o2_c --> 2.0 ficytcc_c + h2o_c + 4.0 h_e
17528
CYOR3m_FWD_CPLX8J2-42
4.27350427350427e-6*mu CPLX8J2-42 + 2.0 ficytcc_c + h_c + mql7_c --> 2.0 focytcc_c + 3.0 h_e + mqn7_c
17529
CYSGLYt2ir_FWD_BSU07840-MONOMER
4.27350427350427e-6*mu BSU07840-MONOMER + cgly_e + h_e --> cgly_c + h_c
17530
CYSS_2_FWD_BSU00730-MONOMER
4.27350427350427e-6*mu BSU00730-MONOMER + acser_c + h2s_c --> ac_c + cys__L_c
17531
CYSTGL_FWD_BSU27250-MONOMER
4.27350427350427e-6*mu BSU27250-MONOMER + cyst__L_c + h2o_c --> 2obut_c + cys__L_c + nh4_c
17532
CYSTL_FWD_BSU11880-MONOMER
4.27350427350427e-6*mu BSU11880-MONOMER + cyst__L_c + h2o_c --> hcys__L_c + nh4_c + pyr_c
17533
CYSTS_FWD_BSU27260-MONOMER
4.27350427350427e-6*mu BSU27260-MONOMER + hcys__L_c + ser__L_c --> cyst__L_c + 

17989
GMPS2_FWD_BSU06360-MONOMER
4.27350427350427e-6*mu BSU06360-MONOMER + atp_c + gln__L_c + h2o_c + xmp_c --> amp_c + glu__L_c + gmp_c + 2.0 h_c + ppi_c
17990
GMPt6_REV_BSU07840-MONOMER
4.27350427350427e-6*mu BSU07840-MONOMER + gmp_c + h_c --> gmp_e + h_e
17991
GMPt6_FWD_BSU07840-MONOMER
4.27350427350427e-6*mu BSU07840-MONOMER + gmp_e + h_e --> gmp_c + h_c
17992
GNKr_REV_BSU40060-MONOMER
6pgc_c + 4.27350427350427e-6*mu BSU40060-MONOMER + adp_c + h_c --> atp_c + glcn__D_c
17993
GNKr_FWD_BSU40060-MONOMER
4.27350427350427e-6*mu BSU40060-MONOMER + atp_c + glcn__D_c --> 6pgc_c + adp_c + h_c
17994
GPDDA1_FWD_BSU02130-MONOMER
4.27350427350427e-6*mu BSU02130-MONOMER + g3pc_c + h2o_c --> chol_c + glyc3p_c + h_c
17995
GPDDA2_FWD_BSU02130-MONOMER
4.27350427350427e-6*mu BSU02130-MONOMER + g3pe_c + h2o_c --> etha_c + glyc3p_c + h_c
17996
GPDDA4_FWD_BSU02130-MONOMER
4.27350427350427e-6*mu BSU02130-MONOMER + g3pg_c + h2o_c --> glyc3p_c + glyc_c + h_c
17997
GRTT_FWD_BSU24280-MONOMER
4.27350427350427

18319
MLTG2_FWD_BSU34560-MONOMER
4.27350427350427e-6*mu BSU34560-MONOMER + h2o_c + maltttr_c --> glc__D_c + malttr_c
18320
MLTG3_FWD_BSU34560-MONOMER
4.27350427350427e-6*mu BSU34560-MONOMER + h2o_c + maltpt_c --> glc__D_c + maltttr_c
18321
MLTG4_FWD_BSU34560-MONOMER
4.27350427350427e-6*mu BSU34560-MONOMER + h2o_c + malthx_c --> glc__D_c + maltpt_c
18322
MLTG5_FWD_BSU34560-MONOMER
4.27350427350427e-6*mu BSU34560-MONOMER + h2o_c + malthp_c --> glc__D_c + malthx_c
18323
MLTG6_FWD_BSU34560-MONOMER
4.27350427350427e-6*mu BSU34560-MONOMER + dextrin_c + 2.0 h2o_c --> 2.0 glc__D_c
18324
MLTG7_FWD_BSU34560-MONOMER
4.27350427350427e-6*mu BSU34560-MONOMER + h2o_c + isomal_c --> 2.0 glc__D_c
18325
MMSAD1_FWD_BSU39760-MONOMER
2mop_c + 4.27350427350427e-6*mu BSU39760-MONOMER + coa_c + nad_c --> co2_c + nadh_c + ppcoa_c
18326
MMSAD1_FWD_CPLX-8648
2mop_c + 4.27350427350427e-6*mu CPLX-8648 + coa_c + nad_c --> co2_c + nadh_c + ppcoa_c
18327
MMSAD2_FWD_BSU39760-MONOMER
4.27350427350427e-6*mu BSU39760-MON

18692
SPMDAT1_FWD_BSU26600-MONOMER
4.27350427350427e-6*mu BSU26600-MONOMER + accoa_c + spmd_c --> N1aspmd_c + coa_c + h_c
18693
SPMDAT3_FWD_BSU26600-MONOMER
4.27350427350427e-6*mu BSU26600-MONOMER + 2.0 accoa_c + sprm_c --> 2.0 coa_c + diasprm_c + 2.0 h_c
18694
SPMDt3i_REV_BSU26590-MONOMER
4.27350427350427e-6*mu BSU26590-MONOMER + h_e + spmd_c --> h_c + spmd_e
18695
SPMS_FWD_BSU37500-MONOMER
4.27350427350427e-6*mu BSU37500-MONOMER + ametam_c + ptrc_c --> 5mta_c + h_c + spmd_c
18696
SPRMS_FWD_BSU37500-MONOMER
4.27350427350427e-6*mu BSU37500-MONOMER + ametam_c + spmd_c --> 5mta_c + h_c + sprm_c
18697
SRB_Lt_REV_BSU07840-MONOMER
4.27350427350427e-6*mu BSU07840-MONOMER + srb__L_c --> srb__L_e
18698
SRB_Lt_FWD_BSU07840-MONOMER
4.27350427350427e-6*mu BSU07840-MONOMER + srb__L_e --> srb__L_c
18699
SSALy_FWD_BSU03910-MONOMER
4.27350427350427e-6*mu BSU03910-MONOMER + h2o_c + nadp_c + sucsal_c --> 2.0 h_c + nadph_c + succ_c
18700
SUCBZL_FWD_BSU30790-MONOMER
4.27350427350427e-6*mu BSU30790-MONOME

### 7) Incorporate remaining biomass constituents
There are leftover components from the *i*JO1366 biomass equation that either: 
1. have no mechanistic function in the model (glycogen)
2. are cofactors that are regenerated (nad)

Applies demands and coefficients from the *i*JO1366 biomass objective function

In [16]:
me.ngam = 1.
me.gam = 34.98
me.unmodeled_protein_fraction = .36

biomass_constituents = {
    "glycogen_c": -.023 / (me.metabolites.glycogen_c.formula_weight / 1000.),
    "nad_c": -.001831,
    "udcpdp_c": -5.5e-05,
    "coa_c": -0.000576,
    "ribflv_c": -0.000223,
    "nadp_c": -0.000447,
    "mlthf_c": -0.000223,
    "thf_c": -0.000223,
    "10fthf_c": -0.000223
}


rxn = cobrame.SummaryVariable('biomass_constituent_demand')
me.add_reactions([rxn])
rxn.add_metabolites(biomass_constituents)
constituent_mass = sum(me.metabolites.get_by_id(c).formula_weight / 1000. * -v
                     for c, v in biomass_constituents.items())
rxn.lower_bound = mu
rxn.upper_bound = mu
rxn.add_metabolites({me.metabolites.constituent_biomass: constituent_mass})

/home/jt/UCSD/cobrame-master/cobrame/core/model.py:103 UserWarning: Adding ATPM reaction to model
/home/jt/UCSD/cobrame-master/cobrame/core/model.py:86 UserWarning: Adding GAM reaction to model


 #### Lipid components
 Metabolites and coefficients from *i*JO1366 biomass objective function

In [17]:
# Find biomass constituents with 3 numbers followed by a compartment in the BOF
lipid = re.compile('\d{3}_.')
lipid_demand = {}
for key, value in ijo.reactions.BIOMASS_BS_10.metabolites.items():
    if lipid.search(key.id):
        lipid_demand[key.id] = abs(value)
                
for met, requirement in lipid_demand.items():
    component_mass = me.metabolites.get_by_id(met).formula_weight / 1000.
    rxn = cobrame.SummaryVariable('Demand_' + met)
    me.add_reactions([rxn])
    rxn.add_metabolites({met: -1 * requirement,
                         'lipid_biomass': component_mass * requirement})
    rxn.lower_bound = mu
    rxn.upper_bound = 1000.

# Kdo2lipid4
#requirement = 0.01945  # in mmol/gDW
#met = me.metabolites.get_by_id('kdo2lipid4_e')
#component_mass = met.formula_weight / 1000.
#rxn = cobrame.SummaryVariable('Demand_' + met.id)
#me.add_reactions([rxn])

#rxn.add_metabolites({met.id : -1.*requirement,
#                     'lipid_biomass': component_mass * requirement})
#rxn.lower_bound = mu
#rxn.upper_bound = mu

In [18]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

18874
ATPM
atp_c + h2o_c --> adp_c + h_c + pi_c
18875
GAM
34.98 atp_c + 34.98 h2o_c --> 34.98 adp_c + 34.98 h_c + 34.98 pi_c
18876
biomass_constituent_demand
0.000223 10fthf_c + 0.000576 coa_c + 0.14185219494685478 glycogen_c + 0.000223 mlthf_c + 0.001831 nad_c + 0.000447 nadp_c + 0.000223 ribflv_c + 0.000223 thf_c + 5.5e-05 udcpdp_c --> 0.025423944002581 constituent_biomass


#### DNA Demand Requirements
Added based on growth rate dependent DNA levels as in [O'brien EJ et al 2013](https://www.ncbi.nlm.nih.gov/pubmed/24084808)

In [19]:
dna_demand_stoich, dna_demand_bound = ecolime.dna_replication.return_gr_dependent_dna_demand(
    me, me.global_info['GC_fraction'])

dna_replication = cobrame.SummaryVariable("DNA_replication")
me.add_reaction(dna_replication)
dna_replication.add_metabolites(dna_demand_stoich)
dna_biomass = cobrame.Constraint("DNA_biomass")

dna_mw = 0
dna_mw_no_ppi = ecolime.dna_replication.get_dna_mw_no_ppi_dict(me)
for met, value in me.reactions.DNA_replication.metabolites.items():
    if met.id != 'ppi_c':
        dna_mw -= value * dna_mw_no_ppi[met.id.replace('_c','')] / 1000.
        
dna_replication.add_metabolites({dna_biomass: dna_mw})
dna_replication.lower_bound = dna_demand_bound 
dna_replication.upper_bound = dna_demand_bound 


**Note**: From this point forward, executing every codeblock should result in a solveable ME-model

------

## Part 2: Add metastructures to solving ME-model
This includes:
1. ribosome
2. RNA polymerase
3. charged_tRNAs

Sometimes multiple entities can perform the same role. To prevent a combinatorial explosion of possibilities, we can create  "generic" version, where any of those entities can fill in.

In [20]:
for generic, components in generics.generic_dict.items():
    cobrame.GenericData(generic, me, components).create_reactions()

KeyError: 'BSU_RRNA_15'

### 1) Add ribosome
This uses the ribosome composition definition in **ecolime/ribosome.py**

In [ ]:
ecolime.ribosome.add_ribosome(me, verbose=False)

In [ ]:
last = 19652;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

### 2) Add charged tRNA reactions

The tRNA charging reactions were automatically added when loading the genome from the genbank file. However, the charging reactions still need to be made aware of the tRNA synthetases which are responsible.

Uses **trna_charging.py**

In [ ]:
aa_synthetase_dict = ecolime.trna_charging.amino_acid_trna_synthetase
for data in me.tRNA_data:
    data.synthetase = str(aa_synthetase_dict[data.amino_acid])

Generic charged tRNAs are added to translation reactions via SubreactionData below.

All new data added in this block contained in **ecolime/translation.py**

In [ ]:
ecolime.translation.add_charged_trna_subreactions(me)
for data in me.translation_data:
    data.add_initiation_subreactions(start_codons=translation.translation_start_codons,
                                    start_subreactions=set(translation.initiation_subreactions.keys()))

    data.add_elongation_subreactions(elongation_subreactions=set(translation.elongation_subreactions.keys()))

    data.add_termination_subreactions(translation_terminator_dict=translation.translation_stop_dict)

In [ ]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

### 3) Add Transcription Metacomplexes
#### RNA Polymerase

Data for RNA_polymerase composition fround in **ecolime/transcription**

Uses *tu_df* from **TUs_from_ecocyc.txt**, above

In [ ]:
for met in transcription.rna_polymerases:
    rnap_obj = cobrame.RNAP(met)
    me.add_metabolites(rnap_obj)
transcription.add_rna_polymerase_complexes(me, verbose=False)

# associate the correct RNA_polymerase and factors to TUs
sigma_to_rnap_dict = transcription.sigma_factor_complex_to_rna_polymerase_dict
for tu_id in tu_df.index:
    transcription_data = me.process_data.get_by_id(tu_id)
    sigma = tu_df.sigma[tu_id]
    rna_polymerase = sigma_to_rnap_dict[sigma]
    transcription_data.RNA_polymerase = rna_polymerase

#### Degradosome (both for RNA degradation and RNA splicing)

All new data contained in **transcription.py**

In [ ]:
me.add_metabolites([cobrame.Complex('RNA_degradosome')])
data = cobrame.ComplexData('RNA_degradosome', me)
for subunit, value in transcription.rna_degradosome.items():
    data.stoichiometry[subunit] = value
data.create_complex_formation(verbose=False)

# Used for RNA splicing
data = cobrame.SubreactionData('RNA_degradation_machine', me)
data.enzyme = 'RNA_degradosome'

data = cobrame.SubreactionData('RNA_degradation_atp_requirement', me)
# .25 water equivaltent for atp hydrolysis per nucleotide
data.stoichiometry = {'atp_c': -.25, 'h2o_c': -.25, 'adp_c': .25,
                      'pi_c': .25, 'h_c': .25}

transcription.add_rna_splicing(me)

In [ ]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

------
## Part 3: Add remaining modifications
rRNA modifications handled in *add_ribosome*

### 1) Add complex modifications
*complex_modification_dict* from **protein_modification.text**, above

The rest of the new data contained in **ecolime/modifications.py**

In [ ]:
for complex_id, info in complex_modification_dict.items():
    modifications = {}
    for mod, value in info['modifications'].items():
        # stoichiometry of modification determined in 
        # subreaction_data.stoichiometry
        modifications['mod_' + mod] = abs(value)
    me.process_data.get_by_id(complex_id).subreactions = modifications

# Adds modification data for more complicated enzyme modifications
# (ie, iron sulfur cluster modification)
ecolime.modifications.add_modification_procedures(me)

# add formation reactions for each of the ComplexDatas
for cplx_data in me.complex_data:
    formation = cplx_data.formation
    if formation:
        formation.update()
    else:
        cplx_data.create_complex_formation()

### 2) Add tRNA mods and asocciate them with tRNA charging reactions
New data from:
1. **ecolime/trna_charging.py** (read via *add_tRNA_modification_procedures()*)
2. **post_transcriptional_modification_of_tRNA.txt** (modification types per tRNA)


In [ ]:
# Add tRNA modifications to ME-model
ecolime.trna_charging.add_trna_modification_procedures(me)

# trna_modifications = {tRNA_id: {modifications: count}}
trna_modifications=flat_files.get_trna_modification_targets()
for trna in trna_modifications:
    for data in me.process_data.query(trna):
        data.subreactions = trna_modifications[trna]

In [ ]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

---
## Part 4: Add remaining subreactions
### 1) Add translation related subreactions
All new data from **ecolime/translation.py**

In [ ]:
# add the translation subreaction data objects to model
translation.add_translation_subreactions_to_model(me)

# add translation subreaction data to reactions
methionine_cleaved=translation.methionine_cleaved
folding_dict=translation.folding_dict

for data in me.translation_data:
    locus_id = data.id
    if locus_id in methionine_cleaved:
        data.subreactions['N_terminal_methionine_cleavage'] = 1

    for folding_type in folding_dict:
        if locus_id in folding_dict[folding_type]:
            data.subreactions[folding_type] = 1

    # This block was ran above, but should be ran again to 
    # incorporate any subreactions not added previously
    data.add_initiation_subreactions(
        start_codons=translation.translation_start_codons,
        start_subreactions=set(translation.initiation_subreactions.keys()))
    data.add_elongation_subreactions(
        elongation_subreactions=set(translation.elongation_subreactions.keys()))
    data.add_termination_subreactions(
        translation_terminator_dict=translation.translation_stop_dict)

    # add organism specific subreactions associated with peptide processing
    for subrxn in translation.peptide_processing_subreactions:
        data.subreactions[subrxn] = 1

In [ ]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

### 2) Add transcription related subreactions
All new data from **ecolime/transcription.py**

In [ ]:
for subreaction in transcription.transcription_subreactions:
    subreaction_data = cobrame.SubreactionData(subreaction, me)
    enzymes = transcription.transcription_subreactions[subreaction]['enzymes']
    subreaction_data.stoichiometry = transcription.transcription_subreactions[subreaction]['stoich']
    subreaction_data.enzyme = enzymes

for transcription_data in me.transcription_data:
    # Assume false if not in tu_df
    rho_dependent = tu_df.rho_dependent.get(transcription_data.id, False)
    rho = 'dependent' if rho_dependent else 'independent'
    stable = 'stable' if transcription_data.codes_stable_rna else 'normal'
    transcription_data.subreactions['Transcription_%s_rho_%s' % (stable,
                                                                 rho)] = 1

In [ ]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

----
## Part 5: Add in translocation

New data from:
1. **peptide_compartment_and_pathways.txt** (Protein compartment and translocation pathway for each membrane complex)
2. **ecolime/translocation.py** (definitions of each translocation pathway)

In [ ]:
# Add TranslocationData
transloc = pandas.read_csv(join(flat_files.ecoli_files_dir,"peptide_compartment_and_pathways2.txt"),
                           sep='\t', comment="#")
for pathway, info in ecolime.translocation.pathway.items():
    if 'alt' not in pathway:
        transloc_data = cobrame.TranslocationData(pathway + '_translocation', me)
    else:
        transloc_data = cobrame.TranslocationData(pathway.replace('_alt', '_translocation_alt'), me)
    transloc_data.enzyme_dict = info['enzymes']
    transloc_data.keff = info['keff']
    transloc_data.length_dependent_energy = info['length_dependent_energy']
    transloc_data.stoichiometry = info['stoichiometry']

# Associate data and add translocation reactions
ecolime.translocation.add_translocation_pathways(me, transloc, membrane_constraints = False)

# Update stoichiometry of membrane complexes
# new_stoich = {complex_id: protein_w_compartment}
new_stoich = defaultdict(dict)
for cplx, row in transloc.set_index('Complex').iterrows():
    if cplx == 'EG10544-MONOMER':
        continue
    protein = row.Protein.split('(')[0] + '_' + row.Protein_compartment
    value = me.process_data.get_by_id(cplx).stoichiometry['protein_' + row.Protein.split('(')[0]]
    new_stoich[cplx]['protein_' + protein] = float(value)

for cplx, stoich in new_stoich.items():
    complex_data = me.process_data.get_by_id(cplx)
    for met, value in stoich.items():
        complex_data.stoichiometry.pop(met[0:13])
        complex_data.stoichiometry[met] = value
        complex_data.formation.update()
    # Complex ids in protein compartment file doesn't include mods
    # Some have multiple alternative modifications so must loop through these
    for complex_data in me.process_data.query(cplx + '_mod_'):
        for met, value in stoich.items():
            complex_data.stoichiometry.pop(met[0:13])
            complex_data.stoichiometry[met] = value
            complex_data.formation.update()

In [ ]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

---
## Part 6: Add Cell Wall Components
All new data from **ecolime/translocation.py**

In [ ]:
compartment_dict = {}
for prot, compartment in transloc.set_index('Protein').Protein_compartment.to_dict().items():
    compartment_dict[prot.split('(')[0]] = compartment

#### Add lipid modification SubreactionData

In [ ]:
lipid_modifications = ecolime.translocation.lipid_modifications

for lipid in lipid_modifications:
    data = cobrame.SubreactionData('mod_' + lipid, me)
    data.stoichiometry = {lipid: -1, 'g3p_c': 1}
    data.enzyme = ['Lgt_MONOMER', 'LspA_MONOMER']
    # The element contribution is based on the lipid involved in the 
    # modification, so calculate based on the metabolite formula
    data._element_contribution = data.calculate_element_contribution()

data = cobrame.SubreactionData('mod2_pg160_p', me)
data.stoichiometry = {'pg160_p': -1, '2agpg160_p': 1}
data.enzyme = 'EG10168-MONOMER'
data._element_contribution = data.calculate_element_contribution()

data = cobrame.SubreactionData('mod2_pe160_p', me)
data.stoichiometry = {'pe160_p': -1, '2agpe160_p': 1}
data.enzyme = 'EG10168-MONOMER'
data._element_contribution = data.calculate_element_contribution()
    
ecolime.translocation.add_lipoprotein_formation(me, compartment_dict, 
                                                membrane_constraints=False)

#### Correct complex formation IDs if they contain lipoproteins

In [ ]:
for gene in ecolime.translocation.lipoprotein_precursors.values():
    compartment = compartment_dict.get(gene)
    for rxn in me.metabolites.get_by_id('protein_' + gene + '_' + compartment).reactions:
        if isinstance(rxn, cobrame.ComplexFormation):
            data = me.process_data.get_by_id(rxn.complex_data_id)
            value = data.stoichiometry.pop('protein_' + gene + '_' + compartment)
            data.stoichiometry['protein_' + gene + '_lipoprotein' + '_' + compartment] = value
            rxn.update()

#### Braun's lipoprotein demand
Metabolites and coefficients as defined in [Liu et al 2014](http://bmcsystbiol.biomedcentral.com/articles/10.1186/s12918-014-0110-6)

In [ ]:
rxn = cobrame.SummaryVariable('core_structural_demand_brauns')
met1 = me.metabolites.get_by_id('murein5px4p_p')
met1_mass = met1.formula_weight / 1000.
met2 = me.metabolites.get_by_id('protein_b1677_lipoprotein_Outer_Membrane')
me.add_reactions([rxn])
# biomass of lipoprotein accounted for in translation and lipid modification
rxn.add_metabolites({met1 : -0.013894, met2: -0.003597, 'peptidoglycan_biomass':(0.013894 * met1_mass)},
                    combine=False)
rxn.lower_bound = mu
rxn.upper_bound = mu

In [ ]:
last = i+1;
reactionNumber = len(me.reactions);
for i in range(last,reactionNumber):
    rxn = me.reactions[i]
    print(i)
    print(rxn)
    print(rxn.reaction)

-----
## Part 7: Set keffs

Either entirely based on SASA or using fit keffs from [Ebrahim et al 2016](https://www.ncbi.nlm.nih.gov/pubmed/27782110?dopt=Abstract)

In [2]:
keff_list = []
keffs = flat_files.get_reaction_keffs(me, verbose=True)
for reaction_id, keff in keffs.items():
    if keff > 3000:
        keff = 3000.
    elif keff < .01:
        keff = .01
    keff_list.append(keff)
    me.reactions.get_by_id(reaction_id).keff = keff
    me.reactions.get_by_id(reaction_id).update()

# Keffs that were not set in the above block
me.process_data.N_terminal_methionine_cleavage.keff = 1339.4233102860871
me.process_data.peptide_deformylase_processing.keff = 1019.5963333345715
me.reactions.get_by_id('GLUTRR_FWD_CPLX0-3741').keff = 3000 # 3269.0108007383374
me.process_data.fmet_addition_at_START.keff = 1540.4356849968603
me.process_data.ribosome_recycler.keff = 1059.6910912619182
me.process_data.UAG_PrfA_mono_mediated_termination.keff = 1721.7910609284945
me.process_data.UGA_PrfB_mono_mediated_termination.keff = 1700.2966587695353
me.process_data.UAA_generic_RF_mediated_termination.keff = 1753.4238515034572

NameError: name 'flat_files' is not defined

-----
## Part 8: Model updates and corrections

In [ ]:
# Add reaction subsystems from iJO to model
for rxn in ijo.reactions:
    if rxn.id in me.process_data:
        data = me.process_data.get_by_id(rxn.id)
    else:
        continue
    for r in data.parent_reactions:
        r.subsystem = rxn.subsystem

#### Corrections and final updates

In [ ]:
ecolime.corrections.correct_reaction_stoichiometries(me, join(flat_files.ecoli_files_dir, 
                                                              'iJL1678b_model_changes.xlsx'))
# RNA_dummy, TU_b3247, TU_b3705 do not have RNAP, this is set as the most common RNAP
for data in me.transcription_data:
    if len(data.RNA_polymerase) == 0:
        data.RNA_polymerase = 'RNAP70-CPLX'
        
# If lower_bound open, model feeds G6P into EDD
me.reactions.EX_pqq_e.lower_bound = 0
me.reactions.EX_pqq_e.upper_bound = 0

# cobalamin is not in glucose M9 media
me.reactions.EX_cbl1_e.lower_bound = 0

me.process_data.PPKr.lower_bound = 0.
me.process_data.PPKr.update_parent_reactions()
    

# This enyzme is involved in catalyzing this reaction
sub = cobrame.SubreactionData('EG12450-MONOMER_activity', me)
sub.enzyme = 'EG12450-MONOMER'
me.process_data.NHFRBO.subreactions['EG12450-MONOMER_activity'] = 1

#### Add enzymatic coupling for "carriers"
These are enzyme complexes that act as metabolites in a metabolic reaction (i.e. are metabolites in iJO1366)

In [ ]:
for data in me.stoichiometric_data:
    if data.id == 'dummy_reaction':
        continue
        
    for met, value in data.stoichiometry.items():
        if not isinstance(me.metabolites.get_by_id(met), cobrame.Complex) or value > 0:
            continue
            
        subreaction_id = met + '_carrier_activity'
        if subreaction_id not in me.process_data:           
            sub = cobrame.SubreactionData(met + '_carrier_activity', me)
            sub.enzyme = met
        data.subreactions[subreaction_id] = abs(value)

----
## Part 9: Update and save

In [ ]:
me.reactions.dummy_reaction_FWD_SPONT.objective_coefficient = 1.
me.reactions.EX_glc__D_e.lower_bound = -1000
me.reactions.EX_o2_e.lower_bound = -1000
me.ngam = 1.
me.gam = 34.98
me.unmodeled_protein_fraction = .36

In [ ]:
me.update()
me.prune()

### Add remaining complex formulas and compartments to model

In [ ]:
# Update a second time to incorporate all of the metabolite formulas corectly
for r in me.reactions.query('formation_'):
    r.update()

# Update complex formulas
df = pandas.read_table(join(flat_files.ecoli_files_dir, 'modification.txt'),
                            names=['mod', 'formula','na'])
df = df.drop('na', axis=1).set_index('mod').dropna(how='any')
modification_formulas = df.T.to_dict()
formulas.add_remaining_complex_formulas(me, modification_formulas)

me.metabolites.get_by_id('CPLX0-782_mod_1:2fe2s_mod_1:4fe4s').formula = 'C3164Fe6H5090N920O920S50'
me.metabolites.get_by_id('EG50003-MONOMER_mod_pan4p_mod_lipo').formula = 'C387H606N95O142PS4'
# Update reactions affected by formula update 
for r in me.reactions.query('_mod_lipo'):
    r.update()
for r in me.reactions.query('_mod_glycyl'):
    r.update()
    
# add metaboolite compartments
compartments.add_compartments_to_model(me)

In [ ]:
n_genes = len(me.metabolites.query(re.compile('RNA_b[0-9]')))
print("number of genes in the model %d (%.2f%%)" % (n_genes, n_genes * 100. / (1678)))

In [ ]:
with open("./me_models/iJL1678b.pickle", "wb") as outfile:
    pickle.dump(me, outfile)

In [ ]:
save_json_me_model(me, './me_models/iJL1678b.json')